In [1]:
import plotly.express as px
import pandas as pd
import geopandas as gpd
import matplotlib.pyplot as plt
import json
import sys

#file import
baltimore_geojson_file = "Community_Borders.txt"
baltimore_map = gpd.read_file(baltimore_geojson_file)
data = baltimore_map
geojson_data = data
with open(baltimore_geojson_file, "r") as file:
    geo_as_json = json.load(file)
    
# Load your CSV dataset
data = pd.read_csv('Baltimore_HFAI.csv')

# Set a higher recursion limit
sys.setrecursionlimit(10**8)  # Adjust the value as needed
gdf = gpd.GeoDataFrame.from_features(geojson_data)
merged_df = gdf.merge(data, left_on='CSA2010', right_on='CSA2010', how='inner')


# Plot the GeoDataFrame using Plotly
fig = px.choropleth_mapbox(
    merged_df,
    geojson=geojson_data,
    featureidkey="properties.OBJECTID",
    locations=merged_df.index,
    color="2015",
    color_continuous_scale="darkmint",
    mapbox_style="carto-positron",
    center={"lat": merged_df.geometry.centroid.y.mean(), "lon": merged_df.geometry.centroid.x.mean()},
    zoom=10,
    opacity=0.65,
    width=600,
    height=600
)
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":100}, coloraxis_colorbar=dict(
        title='',
        orientation='h',  # 'h' for horizontal
        x=0.5,  # Center align the color bar on the x-axis
        xanchor='center',  # Anchor the color bar at the center
        y=-0.2,  # Position the color bar slightly below the plot area
        yanchor='bottom'  # Anchor the color bar at the bottom
    ),
    annotations=[
        dict(
            text="Social Vulnerability Index Percentile",
            showarrow=False,
            xref="paper",
            yref="paper",
            x=0.5,
            y=-0.08,
            xanchor="center",
            yanchor="bottom",
            align="center",
            font=dict(size=14)
        )
    ])

fig.show()
fig.write_html("Baltimore_HFAI.html")